In [1]:
import numpy as np # library to handle data in a vectorized manner

import pandas as pd # library for data analsysis
pd.set_option("display.max_columns", None)
pd.set_option("display.max_rows", None)

import json # library to handle JSON files


from geopy.geocoders import Nominatim # convert an address into latitude and longitude values
! pip install geocoder
import geocoder

import requests # library to handle requests
from bs4 import BeautifulSoup # library to parse HTML and XML documents

from pandas.io.json import json_normalize # tranform JSON file into a pandas dataframe

# Matplotlib and associated plotting modules
import matplotlib.cm as cm
import matplotlib.colors as colors

# import k-means from clustering stage
from sklearn.cluster import KMeans

! pip install folium

import folium # map rendering library

print("Libraries imported.")

Libraries imported.


In [2]:
#request for page with the required content
data = requests.get("https://en.wikipedia.org/wiki/Category:Suburbs_in_Kuala_Lumpur").text

In [3]:
#html to bs4 object
soup = BeautifulSoup(data, 'html.parser')

In [4]:
neighborhoodList = []

In [5]:
#Find neighborhood information and store in list
for row in soup.find_all("div", class_="mw-category")[0].findAll("li"):
    neighborhoodList.append(row.text)

In [6]:
kl_df = pd.DataFrame({"Neighborhood": neighborhoodList})

kl_df.head()

Neighborhood
0             Alam Damai
1   Ampang, Kuala Lumpur
2       Bandar Menjalara
3  Bandar Sri Permaisuri
4   Bandar Tasik Selatan

In [7]:
kl_df.shape

(71, 1)

In [8]:
# define a function to get coordinates
def get_latlng(neighborhood):
    lat_lng_coords = None
    # loop until you get the coordinates
    while(lat_lng_coords is None):
        g = geocoder.arcgis('{}, Kuala Lumpur, Malaysia'.format(neighborhood))
        lat_lng_coords = g.latlng
    return lat_lng_coords

In [9]:
#call the function to get the coordinates, store in a new list using list comprehension
coords = [ get_latlng(neighborhood) for neighborhood in kl_df["Neighborhood"].tolist() ]

In [10]:
coords

[[3.0576900000000364, 101.74388000000005],
 [3.1484988508598852, 101.69672774991264],
 [3.1903500000000236, 101.62545000000006],
 [3.1039100000000417, 101.71226000000007],
 [3.072750000000042, 101.71461000000005],
 [3.0827600000000643, 101.72281000000004],
 [3.1292000000000257, 101.67844000000008],
 [3.1292000000000257, 101.67844000000008],
 [3.111020000000053, 101.66283000000004],
 [3.061870000000056, 101.74675000000008],
 [3.147890000000075, 101.69405000000006],
 [3.12916000000007, 101.68406000000004],
 [3.147770000000037, 101.70855000000006],
 [3.0578100000000745, 101.68965000000009],
 [3.1434800000000678, 101.64433000000008],
 [3.1486092228953293, 101.69985445868105],
 [3.129290000000026, 101.69896000000006],
 [3.17381000000006, 101.68276000000009],
 [3.061870000000056, 101.74675000000008],
 [3.163590000000056, 101.69811000000004],
 [3.1479700000000435, 101.66795000000008],
 [3.1364442625375997, 101.69029430612223],
 [3.1578250453611005, 101.69728006780952],
 [3.083300000000065, 10

In [11]:
#Temporary dataframe to store neighborhood coordinates
df_coords = pd.DataFrame(coords, columns=['Latitude', 'Longitude'])

In [12]:
#merge the coordinates into the original dataframe
kl_df['Latitude'] = df_coords['Latitude']
kl_df['Longitude'] = df_coords['Longitude']

In [13]:
print(kl_df.shape)
kl_df

(71, 3)


Neighborhood  Latitude   Longitude
0                     Alam Damai  3.057690  101.743880
1           Ampang, Kuala Lumpur  3.148499  101.696728
2               Bandar Menjalara  3.190350  101.625450
3          Bandar Sri Permaisuri  3.103910  101.712260
4           Bandar Tasik Selatan  3.072750  101.714610
5               Bandar Tun Razak  3.082760  101.722810
6                        Bangsar  3.129200  101.678440
7                   Bangsar Park  3.129200  101.678440
8                  Bangsar South  3.111020  101.662830
9                 Batu 11 Cheras  3.061870  101.746750
10            Batu, Kuala Lumpur  3.147890  101.694050
11                   Brickfields  3.129160  101.684060
12                 Bukit Bintang  3.147770  101.708550
13                   Bukit Jalil  3.057810  101.689650
14                   Bukit Kiara  3.143480  101.644330
15                   Bukit Nanas  3.148609  101.699854
16                Bukit Petaling  3.129290  101.698960
17                   Bukit Tunku  3.173810  101.682760
18          Cheras, Kuala Lumpur  3.061870  101.746750
19                      Chow Kit  3.163590  101.698110
20             Damansara Heights  3.147970  101.667950
21         Damansara Town Centre  3.136444  101.690294
22                    Dang Wangi  3.157825  101.697280
23                 Desa Petaling  3.083300  101.704380
24    Federal Hill, Kuala Lumpur  3.136370  101.685640
25                  Happy Garden  3.201630  101.721070
26  Jalan Cochrane, Kuala Lumpur  3.134630  101.721690
27                       Jinjang  3.209500  101.658740
28    Kampung Baru, Kuala Lumpur  3.165460  101.710280
29         Kampung Datuk Keramat  3.166400  101.730460
30            Kampung Kasipillay  3.177760  101.682400
31         Kampung Padang Balang  3.209430  101.693180
32                        Kepong  3.217500  101.637630
33                   Kepong Baru  3.207771  101.645173
34                   KL Eco City  3.117130  101.673840
35                   Kuchai Lama  3.090690  101.677320
36                 Lembah Pantai  3.121189  101.663889
37                        Maluri  3.147890  101.694050
38                  Medan Tuanku  3.159260  101.698340
39                       Miharja  3.147890  101.694050
40                    Mont Kiara  3.165290  101.652420
41                  Pantai Dalam  3.094760  101.667470
42            Pudu, Kuala Lumpur  3.133540  101.713070
43                     Putrajaya  3.125860  101.718624
44                   Salak South  3.081540  101.696890
45                      Segambut  3.186500  101.667950
46                       Semarak  3.179943  101.721449
47          Sentul, Kuala Lumpur  3.175080  101.693050
48                       Setapak  3.188160  101.704150
49                   Setiawangsa  3.191802  101.740066
50                      Shamelin  3.124570  101.735970
51                  Sri Hartamas  3.162200  101.650360
52                  Sri Petaling  3.072600  101.682520
53                   Sungai Besi  3.049970  101.706030
54            Taman Bukit Maluri  3.200660  101.633370
55               Taman Connaught  3.082690  101.736890
56                    Taman Desa  3.102970  101.684710
57                    Taman Duta  3.155620  101.671840
58                 Taman Ibukota  3.212160  101.715400
59                Taman Len Seng  3.069080  101.742870
60                  Taman Melati  3.223570  101.723990
61                   Taman Midah  3.093590  101.728370
62                     Taman OUG  3.210051  101.634508
63               Taman P. Ramlee  3.193940  101.705730
64               Taman Sri Sinar  3.190070  101.652930
65            Taman Taynton View  3.087070  101.736810
66           Taman Tun Dr Ismail  3.152830  101.622710
67                 Taman U-Thant  3.157700  101.724520
68                   Taman Wahyu  3.222400  101.671730
69                    Titiwangsa  3.180730  101.703210
70                   Wangsa Maju  3.203870  101.737150

In [14]:
kl_df.to_csv("kl_df.csv", index=False)

In [15]:
# get the coordinates of Kuala Lumpur
address = 'Kuala Lumpur, Malaysia'

geolocator = Nominatim(user_agent="user_agent")
location = geolocator.geocode(address)
latitude = location.latitude
longitude = location.longitude
print('The geograpical coordinate of Kuala Lumpur, Malaysia {}, {}.'.format(latitude, longitude))

The geograpical coordinate of Kuala Lumpur, Malaysia 3.1516964, 101.6942371.


In [16]:
#Create map of KL using latitude and longitude values
map_kl = folium.Map(location=[latitude, longitude], zoom_start=11)

# add markers to map
for lat, lng, neighborhood in zip(kl_df['Latitude'], kl_df['Longitude'], kl_df['Neighborhood']):
    label = '{}'.format(neighborhood)
    label = folium.Popup(label, parse_html=True)
    folium.CircleMarker(
        [lat, lng],
        radius=5,
        popup=label,
        color='blue',
        fill=True,
        fill_color='#3186cc',
        fill_opacity=0.7).add_to(map_kl)  
    
map_kl

In [17]:
map_kl.save('map_kl.html')

In [18]:
#Foursquare Credentials and Version
CLIENT_ID = 'YVXYDU1VBNSHJ0KVWV204IGDIJRQ5PCDAKA22I02K14TWV0F' 
CLIENT_SECRET = '40A41DBJ224QM3GWSRSYJNPEW1A2NF3YG0XQ3MVWW3TRZBUK'
VERSION = '20180605' # Foursquare API version

In [20]:
radius = 2000
LIMIT = 100

venues = []

for lat, long, neighborhood in zip(kl_df['Latitude'], kl_df['Longitude'], kl_df['Neighborhood']):
    
    url = "https://api.foursquare.com/v2/venues/explore?client_id={}&client_secret={}&v={}&ll={},{}&radius={}&limit={}".format(
        CLIENT_ID,
        CLIENT_SECRET,
        VERSION,
        lat,
        long,
        radius, 
        LIMIT)
    
    # make the GET request
    results = requests.get(url).json()["response"]['groups'][0]['items']
    print(results)
    
    # return only relevant information for each nearby venue
    for venue in results:
        venues.append((
            neighborhood,
            lat, 
            long, 
            venue['venue']['name'], 
            venue['venue']['location']['lat'], 
            venue['venue']['location']['lng'],  
            venue['venue']['categories'][0]['name']))

[{'reasons': {'count': 0, 'items': [{'summary': 'This spot is popular', 'type': 'general', 'reasonName': 'globalInteractionReason'}]}, 'venue': {'id': '585a7dc38f0be45899c62d08', 'name': 'Food Truck Lake Valley', 'location': {'address': 'Persiaran Suarasa 2', 'lat': 3.0594266808214177, 'lng': 101.74449567398206, 'labeledLatLngs': [{'label': 'display', 'lat': 3.0594266808214177, 'lng': 101.74449567398206}], 'distance': 205, 'postalCode': '43200', 'cc': 'MY', 'city': 'Cheras 9 Miles', 'state': 'Selangor', 'country': 'Malaysia', 'formattedAddress': ['Persiaran Suarasa 2', '43200 Cheras 9 Miles, Selangor', 'Malaysia']}, 'categories': [{'id': '4bf58dd8d48988d1cb941735', 'name': 'Food Truck', 'pluralName': 'Food Trucks', 'shortName': 'Food Truck', 'icon': {'prefix': 'https://ss3.4sqi.net/img/categories_v2/food/streetfood_', 'suffix': '.png'}, 'primary': True}], 'photos': {'count': 0, 'groups': []}}, 'referralId': 'e-0-585a7dc38f0be45899c62d08-0'}, {'reasons': {'count': 0, 'items': [{'summary

[{'reasons': {'count': 0, 'items': [{'summary': 'This spot is popular', 'type': 'general', 'reasonName': 'globalInteractionReason'}]}, 'venue': {'id': '4d24a53acc84721e5e786af6', 'name': 'BackHome Kuala Lumpur', 'location': {'address': '30 Jalan Tun H.S. Lee', 'lat': 3.1487320097070586, 'lng': 101.69788693213052, 'labeledLatLngs': [{'label': 'display', 'lat': 3.1487320097070586, 'lng': 101.69788693213052}], 'distance': 131, 'postalCode': '50000', 'cc': 'MY', 'city': 'Kuala Lumpur', 'state': 'Kuala Lumpur', 'country': 'Malaysia', 'formattedAddress': ['30 Jalan Tun H.S. Lee', '50000 Kuala Lumpur, Kuala Lumpur', 'Malaysia']}, 'categories': [{'id': '4bf58dd8d48988d1ee931735', 'name': 'Hostel', 'pluralName': 'Hostels', 'shortName': 'Hostel', 'icon': {'prefix': 'https://ss3.4sqi.net/img/categories_v2/travel/hostel_', 'suffix': '.png'}, 'primary': True}], 'photos': {'count': 0, 'groups': []}}, 'referralId': 'e-0-4d24a53acc84721e5e786af6-0'}, {'reasons': {'count': 0, 'items': [{'summary': 'Thi

[{'reasons': {'count': 0, 'items': [{'summary': 'This spot is popular', 'type': 'general', 'reasonName': 'globalInteractionReason'}]}, 'venue': {'id': '4b3bf3eef964a520177f25e3', 'name': 'The Waterfront', 'location': {'address': '5, Persiaran Residen', 'lat': 3.1869356044753956, 'lng': 101.62779779782416, 'labeledLatLngs': [{'label': 'display', 'lat': 3.1869356044753956, 'lng': 101.62779779782416}], 'distance': 461, 'postalCode': '52200', 'cc': 'MY', 'neighborhood': 'Desa Park City', 'city': 'Kuala Lumpur', 'state': 'Kuala Lumpur', 'country': 'Malaysia', 'formattedAddress': ['5, Persiaran Residen', '52200 Kuala Lumpur, Kuala Lumpur', 'Malaysia']}, 'categories': [{'id': '4bf58dd8d48988d164941735', 'name': 'Plaza', 'pluralName': 'Plazas', 'shortName': 'Plaza', 'icon': {'prefix': 'https://ss3.4sqi.net/img/categories_v2/parks_outdoors/plaza_', 'suffix': '.png'}, 'primary': True}], 'photos': {'count': 0, 'groups': []}}, 'referralId': 'e-0-4b3bf3eef964a520177f25e3-0'}, {'reasons': {'count': 

[{'reasons': {'count': 0, 'items': [{'summary': 'This spot is popular', 'type': 'general', 'reasonName': 'globalInteractionReason'}]}, 'venue': {'id': '5a7d64311f8ed61372770073', 'name': 'Burger King', 'location': {'lat': 3.101433949498169, 'lng': 101.71246756947359, 'labeledLatLngs': [{'label': 'display', 'lat': 3.101433949498169, 'lng': 101.71246756947359}], 'distance': 276, 'postalCode': '56000', 'cc': 'MY', 'city': 'Kuala Lumpur', 'state': 'KL', 'country': 'Malaysia', 'formattedAddress': ['56000 Kuala Lumpur, KL', 'Malaysia']}, 'categories': [{'id': '4bf58dd8d48988d16e941735', 'name': 'Fast Food Restaurant', 'pluralName': 'Fast Food Restaurants', 'shortName': 'Fast Food', 'icon': {'prefix': 'https://ss3.4sqi.net/img/categories_v2/food/fastfood_', 'suffix': '.png'}, 'primary': True}], 'photos': {'count': 0, 'groups': []}}, 'referralId': 'e-0-5a7d64311f8ed61372770073-0'}, {'reasons': {'count': 0, 'items': [{'summary': 'This spot is popular', 'type': 'general', 'reasonName': 'globalIn

[{'reasons': {'count': 0, 'items': [{'summary': 'This spot is popular', 'type': 'general', 'reasonName': 'globalInteractionReason'}]}, 'venue': {'id': '4d383b35d60c6dcb3bcf75bc', 'name': 'Wak Nan Roti Canai', 'location': {'address': 'Jalan 20/146, Desa Tasik', 'lat': 3.0753049491690807, 'lng': 101.71762994270289, 'labeledLatLngs': [{'label': 'display', 'lat': 3.0753049491690807, 'lng': 101.71762994270289}], 'distance': 439, 'postalCode': '57000', 'cc': 'MY', 'city': 'Sg Besi', 'state': 'Kuala Lumpur', 'country': 'Malaysia', 'formattedAddress': ['Jalan 20/146, Desa Tasik', '57000 Sg Besi, Kuala Lumpur', 'Malaysia']}, 'categories': [{'id': '4bf58dd8d48988d16d941735', 'name': 'Café', 'pluralName': 'Cafés', 'shortName': 'Café', 'icon': {'prefix': 'https://ss3.4sqi.net/img/categories_v2/food/cafe_', 'suffix': '.png'}, 'primary': True}], 'photos': {'count': 0, 'groups': []}}, 'referralId': 'e-0-4d383b35d60c6dcb3bcf75bc-0'}, {'reasons': {'count': 0, 'items': [{'summary': 'This spot is popular

...

[{'reasons': {'count': 0, 'items': [{'summary': 'This spot is popular', 'type': 'general', 'reasonName': 'globalInteractionReason'}]}, 'venue': {'id': '5987a8a32a7ab676699678b9', 'name': 'Simply Ribs (Halal)', 'location': {'address': '36, Lorong Rahim Kajai 14', 'lat': 3.155457310927525, 'lng': 101.62317177378316, 'labeledLatLngs': [{'label': 'display', 'lat': 3.155457310927525, 'lng': 101.62317177378316}], 'distance': 296, 'postalCode': '60000', 'cc': 'MY', 'neighborhood': 'Taman Tun Dr Ismail', 'city': 'Taman Tun Dr Ismail', 'state': 'Kuala Lumpur', 'country': 'Malaysia', 'formattedAddress': ['36, Lorong Rahim Kajai 14', '60000 Taman Tun Dr Ismail, Kuala Lumpur', 'Malaysia']}, 'categories': [{'id': '4bf58dd8d48988d1c4941735', 'name': 'Restaurant', 'pluralName': 'Restaurants', 'shortName': 'Restaurant', 'icon': {'prefix': 'https://ss3.4sqi.net/img/categories_v2/food/default_', 'suffix': '.png'}, 'primary': True}], 'photos': {'count': 0, 'groups': []}, 'venuePage': {'id': '489877424'}}

[{'reasons': {'count': 0, 'items': [{'summary': 'This spot is popular', 'type': 'general', 'reasonName': 'globalInteractionReason'}]}, 'venue': {'id': '4b2cd640f964a520bdc924e3', 'name': 'Cilantro Restaurant & Wine Bar', 'location': {'address': 'MiCasa All Suite Hotel', 'lat': 3.156851963989477, 'lng': 101.7230319911635, 'labeledLatLngs': [{'label': 'display', 'lat': 3.156851963989477, 'lng': 101.7230319911635}], 'distance': 190, 'postalCode': '50400', 'cc': 'MY', 'neighborhood': 'Taman U Thant', 'city': 'Kuala Lumpur', 'state': 'WPKL', 'country': 'Malaysia', 'formattedAddress': ['MiCasa All Suite Hotel', '50400 Kuala Lumpur, WPKL', 'Malaysia']}, 'categories': [{'id': '4bf58dd8d48988d10c941735', 'name': 'French Restaurant', 'pluralName': 'French Restaurants', 'shortName': 'French', 'icon': {'prefix': 'https://ss3.4sqi.net/img/categories_v2/food/french_', 'suffix': '.png'}, 'primary': True}], 'photos': {'count': 0, 'groups': []}}, 'referralId': 'e-0-4b2cd640f964a520bdc924e3-0'}, {'reaso

[{'reasons': {'count': 0, 'items': [{'summary': 'This spot is popular', 'type': 'general', 'reasonName': 'globalInteractionReason'}]}, 'venue': {'id': '55ebee33498e5ccf188f401d', 'name': '心灵之素 Pure Heart Vegeatarian (HQ)', 'location': {'address': '41 Jalan Seri Utara 1', 'crossStreet': 'Seri Utara Off Jalan Ipoh', 'lat': 3.2268240127788594, 'lng': 101.67071675207372, 'labeledLatLngs': [{'label': 'display', 'lat': 3.2268240127788594, 'lng': 101.67071675207372}], 'distance': 505, 'postalCode': '68100', 'cc': 'MY', 'city': 'Kuala Lumpur', 'state': 'Kuala Lumpur', 'country': 'Malaysia', 'formattedAddress': ['41 Jalan Seri Utara 1 (Seri Utara Off Jalan Ipoh)', '68100 Kuala Lumpur, Kuala Lumpur', 'Malaysia']}, 'categories': [{'id': '4bf58dd8d48988d1d3941735', 'name': 'Vegetarian / Vegan Restaurant', 'pluralName': 'Vegetarian / Vegan Restaurants', 'shortName': 'Vegetarian / Vegan', 'icon': {'prefix': 'https://ss3.4sqi.net/img/categories_v2/food/vegetarian_', 'suffix': '.png'}, 'primary': True

[{'reasons': {'count': 0, 'items': [{'summary': 'This spot is popular', 'type': 'general', 'reasonName': 'globalInteractionReason'}]}, 'venue': {'id': '55ac655c498e3f6ad4206916', 'name': 'Mama Kim Sauna Mee', 'location': {'address': '276 Jalan Pahang', 'lat': 3.185023603980431, 'lng': 101.70175367596514, 'labeledLatLngs': [{'label': 'display', 'lat': 3.185023603980431, 'lng': 101.70175367596514}], 'distance': 504, 'postalCode': '53000', 'cc': 'MY', 'city': 'Kuala Lumpur', 'state': 'Kuala Lumpur', 'country': 'Malaysia', 'formattedAddress': ['276 Jalan Pahang', '53000 Kuala Lumpur, Kuala Lumpur', 'Malaysia']}, 'categories': [{'id': '4bf58dd8d48988d16d941735', 'name': 'Café', 'pluralName': 'Cafés', 'shortName': 'Café', 'icon': {'prefix': 'https://ss3.4sqi.net/img/categories_v2/food/cafe_', 'suffix': '.png'}, 'primary': True}], 'photos': {'count': 0, 'groups': []}}, 'referralId': 'e-0-55ac655c498e3f6ad4206916-0'}, {'reasons': {'count': 0, 'items': [{'summary': 'This spot is popular', 'type

[{'reasons': {'count': 0, 'items': [{'summary': 'This spot is popular', 'type': 'general', 'reasonName': 'globalInteractionReason'}]}, 'venue': {'id': '4b50310df964a5204b1e27e3', 'name': 'MadMonkeyz Climbing Gym', 'location': {'address': '19-1/2 Jalan Metro Wangsa', 'crossStreet': 'Section 2, Wangsa Maju', 'lat': 3.2044463220220223, 'lng': 101.73648630386687, 'labeledLatLngs': [{'label': 'display', 'lat': 3.2044463220220223, 'lng': 101.73648630386687}], 'distance': 97, 'postalCode': '53300', 'cc': 'MY', 'city': 'Kuala Lumpur', 'state': 'Kuala Lumpur', 'country': 'Malaysia', 'formattedAddress': ['19-1/2 Jalan Metro Wangsa (Section 2, Wangsa Maju)', '53300 Kuala Lumpur, Kuala Lumpur', 'Malaysia']}, 'categories': [{'id': '50328a4b91d4c4b30a586d6b', 'name': 'Rock Climbing Spot', 'pluralName': 'Rock Climbing Spots', 'shortName': 'Rock Climbing', 'icon': {'prefix': 'https://ss3.4sqi.net/img/categories_v2/parks_outdoors/rockclimbing_', 'suffix': '.png'}, 'primary': True}], 'photos': {'count':

In [21]:
#convert the venues list into a new DataFrame
venues_df = pd.DataFrame(venues)

# define the column names
venues_df.columns = ['Neighborhood', 'Latitude', 'Longitude', 'VenueName', 'VenueLatitude', 'VenueLongitude', 'VenueCategory']

print(venues_df.shape)
venues_df.head()

(7091, 7)


Neighborhood  Latitude  Longitude                      VenueName  \
0   Alam Damai   3.05769  101.74388         Food Truck Lake Valley   
1   Alam Damai   3.05769  101.74388                   Jc Deli 皆喜食坊   
2   Alam Damai   3.05769  101.74388  Pengedar Shaklee Kuala Lumpur   
3   Alam Damai   3.05769  101.74388               Machi Noodle 妈子面   
4   Alam Damai   3.05769  101.74388                  Minang Tomyam   

   VenueLatitude  VenueLongitude       VenueCategory  
0       3.059427      101.744496          Food Truck  
1       3.058397      101.748560   Food & Drink Shop  
2       3.061235      101.740696     Supplement Shop  
3       3.057695      101.746635        Noodle House  
4       3.057185      101.749812  Seafood Restaurant

In [22]:
venues_df.groupby(["Neighborhood"]).count()

Latitude  Longitude  VenueName  VenueLatitude  \
Neighborhood                                                                  
Alam Damai                         100        100        100            100   
Ampang, Kuala Lumpur               100        100        100            100   
Bandar Menjalara                   100        100        100            100   
Bandar Sri Permaisuri              100        100        100            100   
Bandar Tasik Selatan                97         97         97             97   
Bandar Tun Razak                   100        100        100            100   
Bangsar                            100        100        100            100   
Bangsar Park                       100        100        100            100   
Bangsar South                      100        100        100            100   
Batu 11 Cheras                     100        100        100            100   
Batu, Kuala Lumpur                 100        100        100            100   
Brickfields                        100        100        100            100   
Bukit Bintang                      100        100        100            100   
Bukit Jalil                        100        100        100            100   
Bukit Kiara                        100        100        100            100   
Bukit Nanas                        100        100        100            100   
Bukit Petaling                     100        100        100            100   
Bukit Tunku                        100        100        100            100   
Cheras, Kuala Lumpur               100        100        100            100   
Chow Kit                           100        100        100            100   
Damansara Heights                  100        100        100            100   
Damansara Town Centre              100        100        100            100   
Dang Wangi                         100        100        100            100   
Desa Petaling                      100        100        100            100   
Federal Hill, Kuala Lumpur         100        100        100            100   
Happy Garden                       100        100        100            100   
Jalan Cochrane, Kuala Lumpur       100        100        100            100   
Jinjang                            100        100        100            100   
KL Eco City                        100        100        100            100   
Kampung Baru, Kuala Lumpur         100        100        100            100   
Kampung Datuk Keramat              100        100        100            100   
Kampung Kasipillay                 100        100        100            100   
Kampung Padang Balang               95         95         95             95   
Kepong                             100        100        100            100   
Kepong Baru                        100        100        100            100   
Kuchai Lama                        100        100        100            100   
Lembah Pantai                      100        100        100            100   
Maluri                             100        100        100            100   
Medan Tuanku                       100        100        100            100   
Miharja                            100        100        100            100   
Mont Kiara                         100        100        100            100   
Pantai Dalam                       100        100        100            100   
Pudu, Kuala Lumpur                 100        100        100            100   
Putrajaya                          100        100        100            100   
Salak South                        100        100        100            100   
Segambut                           100        100        100            100   
Semarak                            100        100        100            100   
Sentul, Kuala Lumpur               100        100        100            100   
Setapak                            100        100        100            100   
S

In [23]:
print('There are {} uniques categories.'.format(len(venues_df['VenueCategory'].unique())))

There are 308 uniques categories.


In [24]:
#Print out the list of categories
venues_df['VenueCategory'].unique()[:50]

array(['Food Truck', 'Food & Drink Shop', 'Supplement Shop',
       'Noodle House', 'Seafood Restaurant', 'Breakfast Spot',
       'Chinese Restaurant', 'Restaurant', 'Food Court',
       'Vegetarian / Vegan Restaurant', 'Other Great Outdoors',
       'Japanese Restaurant', 'Bubble Tea Shop', 'Coffee Shop',
       'Asian Restaurant', 'Park', 'Indian Restaurant', 'Spa',
       'Snack Place', 'Pet Store', 'Dim Sum Restaurant', 'Dessert Shop',
       'Café', 'Chinese Breakfast Place', 'Outlet Store',
       'Convenience Store', 'Bakery', 'Cantonese Restaurant',
       'Farmers Market', 'Gym / Fitness Center', 'Malay Restaurant',
       'Fast Food Restaurant', 'Middle Eastern Restaurant',
       'Mamak Restaurant', 'Hakka Restaurant', 'Steakhouse',
       'Athletics & Sports', 'College Bookstore', 'Burger Joint',
       'Winery', 'Halal Restaurant', 'Badminton Court', 'Motorcycle Shop',
       'Grocery Store', 'Korean Restaurant', 'Vietnamese Restaurant',
       'Hostel', 'Exhibit', 'South

In [25]:
# one hot encoding
kl_onehot = pd.get_dummies(venues_df[['VenueCategory']], prefix="", prefix_sep="")

# add neighborhood column back to dataframe
kl_onehot['Neighborhoods'] = venues_df['Neighborhood'] 

# move neighborhood column to the first column
fixed_columns = [kl_onehot.columns[-1]] + list(kl_onehot.columns[:-1])
kl_onehot = kl_onehot[fixed_columns]

print(kl_onehot.shape)
kl_onehot.head()

(7091, 309)


Neighborhoods  Accessories Store  Adult Boutique  African Restaurant  \
0    Alam Damai                  0               0                   0   
1    Alam Damai                  0               0                   0   
2    Alam Damai                  0               0                   0   
3    Alam Damai                  0               0                   0   
4    Alam Damai                  0               0                   0   

   American Restaurant  Aquarium  Arcade  Art Gallery  Art Museum  \
0                    0         0       0            0           0   
1                    0         0       0            0           0   
2                    0         0       0            0           0   
3                    0         0       0            0           0   
4                    0         0       0            0           0   

   Arts & Crafts Store  Asian Restaurant  Athletics & Sports  Auditorium  \
0                    0                 0                   0           0   
1                    0                 0                   0           0   
2                    0                 0                   0           0   
3                    0                 0                   0           0   
4                    0                 0                   0           0   

   Auto Garage  Auto Workshop  Automotive Shop  BBQ Joint  Badminton Court  \
0            0              0                0          0                0   
1            0              0                0          0                0   
2            0              0                0          0                0   
3            0              0                0          0                0   
4            0              0                0          0                0   

   Bagel Shop  Bakery  Bar  Baseball Field  Basketball Court  Beer Bar  \
0           0       0    0               0                 0         0   
1           0       0    0               0                 0         0   
2           0       0    0               0                 0         0   
3           0       0    0               0                 0         0   
4           0       0    0               0                 0         0   

   Beer Garden  Betting Shop  Bistro  Board Shop  Bookstore  Botanical Garden  \
0            0             0       0           0          0                 0   
1            0             0       0           0          0                 0   
2            0             0       0           0          0                 0   
3            0             0       0           0          0                 0   
4            0             0       0           0          0                 0   

   Boutique  Bowling Alley  Brazilian Restaurant  Breakfast Spot  Brewery  \
0         0              0                     0               0        0   
1         0              0                     0               0        0   
2         0              0                     0               0        0   
3         0              0                     0               0        0   
4         0              0                     0               0        0   

   Bridal Shop  Bubble Tea Shop  Buffet  Building  Burger Joint  \
0            0                0       0         0             0   
1            0                0       0         0             0   
2            0                0       0         0             0   
3            0                0       0         0             0   
4            0                0       0         0             0   

   Burrito Place  Business Service  Butcher  Café  Camera Store  Campground  \
0              0                 0        0     0             0           0   
1              0                 0        0     0             0           0   
2              0                 0        0     0             0           0   
3              0                 0        0     0             0           0   
4              0       

In [26]:
kl_grouped = kl_onehot.groupby(["Neighborhoods"]).mean().reset_index()

print(kl_grouped.shape)
kl_grouped

(71, 309)


Neighborhoods  Accessories Store  Adult Boutique  \
0                     Alam Damai           0.000000            0.00   
1           Ampang, Kuala Lumpur           0.000000            0.00   
2               Bandar Menjalara           0.000000            0.00   
3          Bandar Sri Permaisuri           0.010000            0.00   
4           Bandar Tasik Selatan           0.010309            0.00   
5               Bandar Tun Razak           0.010000            0.00   
6                        Bangsar           0.000000            0.00   
7                   Bangsar Park           0.000000            0.00   
8                  Bangsar South           0.000000            0.00   
9                 Batu 11 Cheras           0.000000            0.00   
10            Batu, Kuala Lumpur           0.000000            0.01   
11                   Brickfields           0.000000            0.00   
12                 Bukit Bintang           0.000000            0.00   
13                   Bukit Jalil           0.000000            0.00   
14                   Bukit Kiara           0.000000            0.00   
15                   Bukit Nanas           0.000000            0.00   
16                Bukit Petaling           0.010000            0.00   
17                   Bukit Tunku           0.000000            0.00   
18          Cheras, Kuala Lumpur           0.000000            0.00   
19                      Chow Kit           0.000000            0.01   
20             Damansara Heights           0.000000            0.00   
21         Damansara Town Centre           0.000000            0.00   
22                    Dang Wangi           0.000000            0.00   
23                 Desa Petaling           0.000000            0.00   
24    Federal Hill, Kuala Lumpur           0.000000            0.00   
25                  Happy Garden           0.000000            0.00   
26  Jalan Cochrane, Kuala Lumpur           0.000000            0.00   
27                       Jinjang           0.010000            0.00   
28                   KL Eco City           0.000000            0.00   
29    Kampung Baru, Kuala Lumpur           0.000000            0.00   
30         Kampung Datuk Keramat           0.000000            0.00   
31            Kampung Kasipillay           0.000000            0.00   
32         Kampung Padang Balang           0.000000            0.00   
33                        Kepong           0.010000            0.00   
34                   Kepong Baru           0.010000            0.00   
35                   Kuchai Lama           0.000000            0.00   
36                 Lembah Pantai           0.000000            0.00   
37                        Maluri           0.000000            0.01   
38                  Medan Tuanku           0.000000            0.00   
39                       Miharja           0.000000            0.01   
40                    Mont Kiara           0.000000            0.00   
41                  Pantai Dalam           0.000000            0.00   
42            Pudu, Kuala Lumpur           0.010000            0.00   
43                     Putrajaya           0.010000            0.00   
44                   Salak South           0.000000            0.00   
45                      Segambut           0.000000            0.00   
46                       Semarak           0.000000            0.00   
47          Sentul, Kuala Lumpur           0.000000            0.00   
48                       Setapak           0.000000            0.00   
49                   Setiawangsa           0.000000            0.00   
50                      Shamelin           0.000000            0.00   
51                  Sri Hartamas           0.000000            0.00   
52                  Sri Petaling           0.000000            0.00   
53                   Sungai Besi           0.000000            0.00   
54            Taman Bukit Maluri           0.000000            0.00   
55               Taman Connaught           

In [27]:
len(kl_grouped[kl_grouped["Shopping Mall"] > 0])

38

In [29]:
kl_mall = kl_grouped[["Neighborhoods","Shopping Mall"]]
kl_mall.head()


Neighborhoods  Shopping Mall
0             Alam Damai       0.000000
1   Ampang, Kuala Lumpur       0.010000
2       Bandar Menjalara       0.010000
3  Bandar Sri Permaisuri       0.000000
4   Bandar Tasik Selatan       0.010309

In [30]:
kclusters = 3

kl_clustering = kl_mall.drop(["Neighborhoods"], 1)

# run k-means clustering
kmeans = KMeans(n_clusters=kclusters, random_state=0).fit(kl_clustering)

# check cluster labels generated for each row in the dataframe
kmeans.labels_[0:10]

array([2, 0, 0, 2, 0, 2, 1, 1, 0, 2], dtype=int32)

In [31]:
# create a new dataframe that includes the cluster as well as the top 10 venues for each neighborhood.
kl_merged = kl_mall.copy()

# add clustering labels
kl_merged["Cluster Labels"] = kmeans.labels_

In [32]:
kl_merged.rename(columns={"Neighborhoods": "Neighborhood"}, inplace=True)
kl_merged.head()

Neighborhood  Shopping Mall  Cluster Labels
0             Alam Damai       0.000000               2
1   Ampang, Kuala Lumpur       0.010000               0
2       Bandar Menjalara       0.010000               0
3  Bandar Sri Permaisuri       0.000000               2
4   Bandar Tasik Selatan       0.010309               0

In [33]:
#Merge kl_grouped with kl_data to add latitude/longitude for each neighborhood
kl_merged = kl_merged.join(kl_df.set_index("Neighborhood"), on="Neighborhood")

print(kl_merged.shape)
kl_merged.head() # check the last columns!

(71, 5)


Neighborhood  Shopping Mall  Cluster Labels  Latitude   Longitude
0             Alam Damai       0.000000               2  3.057690  101.743880
1   Ampang, Kuala Lumpur       0.010000               0  3.148499  101.696728
2       Bandar Menjalara       0.010000               0  3.190350  101.625450
3  Bandar Sri Permaisuri       0.000000               2  3.103910  101.712260
4   Bandar Tasik Selatan       0.010309               0  3.072750  101.714610

In [34]:
#Sort the results by Cluster Labels
print(kl_merged.shape)
kl_merged.sort_values(["Cluster Labels"], inplace=True)
kl_merged

(71, 5)


Neighborhood  Shopping Mall  Cluster Labels  Latitude  \
70                   Wangsa Maju       0.010000               0  3.203870   
45                      Segambut       0.020000               0  3.186500   
43                     Putrajaya       0.020000               0  3.125860   
53                   Sungai Besi       0.010000               0  3.049970   
38                  Medan Tuanku       0.020000               0  3.159260   
69                    Titiwangsa       0.010000               0  3.180730   
56                    Taman Desa       0.010000               0  3.102970   
57                    Taman Duta       0.020000               0  3.155620   
31            Kampung Kasipillay       0.020000               0  3.177760   
30         Kampung Datuk Keramat       0.010000               0  3.166400   
47          Sentul, Kuala Lumpur       0.010000               0  3.175080   
22                    Dang Wangi       0.020000               0  3.157825   
21         Damansara Town Centre       0.010000               0  3.136444   
20             Damansara Heights       0.020000               0  3.147970   
19                      Chow Kit       0.020000               0  3.163590   
17                   Bukit Tunku       0.020000               0  3.173810   
24    Federal Hill, Kuala Lumpur       0.010000               0  3.136370   
15                   Bukit Nanas       0.020000               0  3.148609   
1           Ampang, Kuala Lumpur       0.010000               0  3.148499   
2               Bandar Menjalara       0.010000               0  3.190350   
4           Bandar Tasik Selatan       0.010309               0  3.072750   
16                Bukit Petaling       0.010000               0  3.129290   
8                  Bangsar South       0.020000               0  3.111020   
50                      Shamelin       0.020000               0  3.124570   
64               Taman Sri Sinar       0.010000               0  3.190070   
36                 Lembah Pantai       0.040000               1  3.121189   
67                 Taman U-Thant       0.030000               1  3.157700   
6                        Bangsar       0.050000               1  3.129200   
7                   Bangsar Park       0.050000               1  3.129200   
42            Pudu, Kuala Lumpur       0.040000               1  3.133540   
11                   Brickfields       0.040000               1  3.129160   
12                 Bukit Bintang       0.030000               1  3.147770   
29    Kampung Baru, Kuala Lumpur       0.030000               1  3.165460   
28                   KL Eco City       0.040000               1  3.117130   
26  Jalan Cochrane, Kuala Lumpur       0.040000               1  3.134630   
51                  Sri Hartamas       0.030000               1  3.162200   
66           Taman Tun Dr Ismail       0.030000               1  3.152830   
40                    Mont Kiara       0.030000               1  3.165290   
62                     Taman OUG       0.000000               2  3.210051   
52                  Sri Petaling       0.000000               2  3.072600   
63               Taman P. Ramlee       0.000000               2  3.193940   
65            Taman Taynton View       0.000000               2  3.087070   
54            Taman Bukit Maluri       0.000000               2  3.200660   
55               Taman Connaught       0.000000               2  3.082690   
61                   Taman Midah       0.000000               2  3.093590   
59                Taman Len Seng       0.000000               2  3.069080   
60                  Taman Melati       0.000000               2  3.223570   
68                   Taman Wahyu       0.000000               2  3.222400   
58                 Taman Ibukota       0.000000               2  3.212160   
0                     Alam Damai       0.000000               2  3.057690   
48                       Setapak       0.000000               2  3.188160   
3          Banda

In [35]:
# create map
map_clusters = folium.Map(location=[latitude, longitude], zoom_start=11)

#Set color scheme for the clusters
x = np.arange(kclusters)
ys = [i+x+(i*x)**2 for i in range(kclusters)]
colors_array = cm.rainbow(np.linspace(0, 1, len(ys)))
rainbow = [colors.rgb2hex(i) for i in colors_array]

# add markers to the map
markers_colors = []
for lat, lon, poi, cluster in zip(kl_merged['Latitude'], kl_merged['Longitude'], kl_merged['Neighborhood'], kl_merged['Cluster Labels']):
    label = folium.Popup(str(poi) + ' - Cluster ' + str(cluster), parse_html=True)
    folium.CircleMarker(
        [lat, lon],
        radius=5,
        popup=label,
        color=rainbow[cluster-1],
        fill=True,
        fill_color=rainbow[cluster-1],
        fill_opacity=0.7).add_to(map_clusters)
       
map_clusters